## ELEX 4653 Quiz 2

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

The `dumps(x)` function in the `json` module returns a string representation of the object `x` formatted as a string.  Write a function `jsonlen(x)` that returns the length of the object `x` when converted to a string using `json.dumps()`.   For example, if `x` is the string "Hello, world!" then `jsonlen(x)` would return `15`.


#### Question 2

Write a function, `unspace(s,r)` where `s` and `r` are strings.  The function should return a string composed of `s` with any space character `' '` replaced with the string `r`. For example `unspace("Quick Brown Fox","_-_")` would return `'Quick_-_Brown_-_Fox'`.

#### Question 3

Write a function `checkit(o)` that obtains `str`(ing) values from the iterable object `o` 
until the value "end" is obtained and then returns the value obtained before "end".
For example,
if `o` returned values from the list `['iwr', 'wbu', 'amz', 'ko', 'end', 'yzwhn']` then `checkit(o)` would return `'ko'`.
Note that the argument `o` is not a list.

#### Question 4

Write a function `exfilter(l)` that test successive integer-like objects in the list `l` by calling these object's `check()` method.
Your function should return a tuple of two lists, the first with the values that did _not_ cause a ValueError exception and the second with the objects that did.
For example, if `x.check()` raises a ValueError exception when `x` is `2` or `4` then `exfilter([1, 2, 3, 4])` would return `([1,3], [2,4])`.

In [5]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.fullmatch(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.fullmatch(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    
    def Q1():
        f,a = jsonlen,randwords(randint(3,5))
        oa = copy.deepcopy(a)
        # r = f(a)
        r = round(f(a),4)
        return r,f"{f.__name__}({oa}) returns {r}"

    def Q2():
        f,a,b = unspace,' '.join(randwords(randint(3,5))),randwords(1,chars="_-*",nl=(1,3))[0]
        ol = copy.deepcopy((a,b))
        r = f(a,b)
        return r,f"{f.__name__}{ol} returns {r}"

    class notalist(list):
        def __init__(self,l):
            super().__init__(l)
        def __getitem__(self,i):
            raise RuntimeError("This object does not support subscripting")
    
    def Q3():
        f = checkit
        # d: two random-length lists with "end" between them
        o = randwords(randint(1,3)) + ['end'] + randwords(randint(1,3))
        oo = copy.deepcopy(o)
        r = checkit(notalist(o))
        return r,f"{f.__name__}({oo}) returns {r}"
        
    def Q4():
        f = exfilter
        l = list(range(1,randint(4,8)))
        random.shuffle(l)
        bad = l[::2]
        class testable(int):
            def __init__(self,x):
                super().__int__()
            def check(self):
                if self in bad:
                    raise ValueError    
        a = [testable(i) for i in l]
        oa = copy.deepcopy(a)
        r = exfilter(a)
        return r,f"{f.__name__}({oa}) returns {r}"
    
    hashvalues = '''
PRYp+uAMo2oc7ggJ+uAMHzbnKYCXa2v8p+ztwU+m
QG+cNenjH3t3Gvsjf3gldZDVGNv+BZQBSbZ6s4WH
2MkX3itCZv+rMg6hyPLsrLuW+p/u84B+gFwR/X4n
g/0JNh2gYJ4+JlQA8BPGKsRlRmEqOXWuzkwUt53B
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                err = f"Error during test {n}: {e}"               
        if testing:
            newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)